#### Carrega as bibliotecas 

In [1]:
import pandas as pd
import folium
import streamlit as st
import datetime as dt
from PIL import Image

import plotly.express as px
import plotly.graph_objects as go
from streamlit_folium import folium_static
from haversine import haversine



2024-10-20 13:05:00.465 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.


 #### Carregar os dados

In [2]:
df = pd.read_csv('C:/Users/carlo/Desktop/Machine Learning/Machine Learning/train2.csv')

In [ ]:
df.head()

#### Tratamento dos dados

In [4]:
#================================
# criando uma cópia do dataframe
#================================

df1 = df.copy()

#=================================
# limpa a coluna que contém 'NaN'
#=================================

col = ['Delivery_person_Age', 'Road_traffic_density',
       'City', 'Festival', 'multiple_deliveries']

for coluna in col:
    linhas_selecionadas = df1[coluna] != 'NaN '
    df1 = df1.loc[linhas_selecionadas, :].copy()



#====================================
# convertendo o formato das colunas
#====================================

df1['Delivery_person_Age'] = df1['Delivery_person_Age'].astype(int)

df1['Delivery_person_Ratings'] = df1['Delivery_person_Ratings'].astype(float)

df1['Order_Date'] = pd.to_datetime(df1['Order_Date'], format='%d-%m-%Y')

df1['Time_Orderd'] = pd.to_datetime(df1['Time_Orderd'])

df1['Time_Order_picked'] = pd.to_datetime(df1['Time_Order_picked'])

df1['multiple_deliveries'] = df1['multiple_deliveries'].astype(int)

#===================================================
#Removendo espaços dentro dos dados da tabela.
#===================================================

df1.loc[:, 'ID'] = df1.loc[:, 'ID'].str.strip()
df1.loc[:, 'Road_traffic_density'] = df1.loc[:, 'Road_traffic_density'].str.strip()
df1.loc[:, 'Type_of_order'] = df1.loc[:, 'Type_of_order'].str.strip()
df1.loc[:, 'Type_of_vehicle'] = df1.loc[:, 'Type_of_vehicle'].str.strip()
df1.loc[:, 'City'] = df1.loc[: , 'City'].str.strip()
df1.loc[:, 'Festival'] = df1.loc[:, 'Festival'].str.strip()
#===================================
#Limpando a coluna de Time_taken
#===================================

df1['Time_taken(min)'] = df1['Time_taken(min)'].apply(lambda x: x.split('(min)')[1])
df1['Time_taken(min)'] =df1['Time_taken(min)'].str.strip(int)



C:\Users\carlo\AppData\Local\Temp\ipykernel_4368\499618087.py:30: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df1['Time_Orderd'] = pd.to_datetime(df1['Time_Orderd'])
C:\Users\carlo\AppData\Local\Temp\ipykernel_4368\499618087.py:32: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df1['Time_Order_picked'] = pd.to_datetime(df1['Time_Order_picked'])


In [ ]:

df1.head()

In [6]:
#Quantidade de pedidodos por dia
# Colunas

coluna = ['ID', 'Order_Date']

#Seleção de linhas
df_aux = df1.loc[:, coluna].groupby('Order_Date').count().reset_index()

# Desenhando o gráfico de linhas


fig = px.bar(df_aux, x = 'Order_Date', y = 'ID')
fig.show()

In [7]:
#Quantidade pedidos por semana

df1['week_of_year'] = df1['Order_Date'].dt.strftime('%U')

df_aux = df1.loc[:,['ID', 'week_of_year']].groupby(['week_of_year']).count().reset_index()
fig = px.line(df_aux, x = 'week_of_year', y = 'ID')

fig.show()


In [8]:
#Distribuição dos pedidos por tipo de tráfego.

df_aux = df1.loc[:, ['ID', 'Road_traffic_density']].groupby(['Road_traffic_density']).count().reset_index()

#df_aux = df_aux.loc[['Road_traffic_density'] != 'NaN ', :]
df_aux['entregas_perc'] = df_aux['ID'] / df_aux['ID'].sum()
 
fig = px.pie(df_aux, values= 'entregas_perc', names='Road_traffic_density', color='Road_traffic_density',
             color_discrete_map={'Low':'lightblue',
                                 'Jam': 'cyan', 
                                 'Medium': 'royalblue',
                                 'High': 'darkblue'})
fig.show()

In [9]:
# Comparação do volme de pedidos por cidade e tipo de tráfego.
df_aux = df1.loc [:, ['ID', 'City', 'Road_traffic_density']].groupby([ 'City','Road_traffic_density']).count().reset_index()


fig = px.scatter(df_aux, x= 'City', y= 'Road_traffic_density', 
                 size='ID', 
                 symbol='City')
fig.update_traces(marker_size=30)
fig.update_layout(scattermode ="group")
fig.show()

In [10]:
# Quantidade de pedidos por entregador por semana.

df_aux1 = df1.loc[:,['ID', 'week_of_year']].groupby(['week_of_year']).count().reset_index()
df_aux2 = df1.loc[:,['Delivery_person_ID', 'week_of_year']].groupby(['week_of_year']).nunique().reset_index()

df_aux = pd.merge(df_aux1, df_aux2, how='inner', on='week_of_year')
df_aux['Orde_by_deliver'] = df_aux['ID'] / df_aux['Delivery_person_ID']

px.line( df_aux, x='week_of_year', y='Orde_by_deliver')

In [11]:
# A  localização central de cada cidade por tipo de tráfego.


df_aux = df1.loc[:, ['City', 'Road_traffic_density', 'Delivery_location_latitude', 'Delivery_location_longitude']].groupby(['City', 'Road_traffic_density']).median()
#df_aux = df_aux.loc[df_aux['City'] != 'NaN ', :]
#df_aux = df_aux.loc[df_aux['Road_traffic_density'] != 'NaN ', :]

fig = px.scatter_mapbox(df1, 
                        lat="Delivery_location_latitude", 
                        lon="Delivery_location_longitude",
                        hover_name="City",
                        hover_data=["Road_traffic_density"],
                        zoom=3,
                        height=600)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.show()